# SWSN Project
Adam Ciesiółka, 150161\
Bogna Kilanowska, 148252\
Maciej Woś, 148276

### 1. Insight into data

In [2]:
import pandas as pd
import numpy as np

As a data-set we used a flavour graph which is represented by two csv files. The first one 'nodes_191120.csv' contains information about all nodes present in the graph.

In [ ]:
df = pd.read_csv('nodes_191120.csv')

'nodes_191120.csv' consists of 6650 rows and 5 columns: 'node_id', 'name' of the ingredient, 'id', 'node_type' determining wheter a node represents an ingredient or compond, 'is_hub'. Dataset lacks of some rows, which can be concludet from the fact, that there are higher node_ids than number of rows.

In [ ]:
print(df.head())

   node_id                    name  id   node_type  is_hub
0        0       1%_fat_buttermilk NaN  ingredient  no_hub
1        1   1%_fat_cottage_cheese NaN  ingredient  no_hub
2        3               10%_cream NaN  ingredient  no_hub
3        4               100%_bran NaN  ingredient  no_hub
4        5  10_inch_flour_tortilla NaN  ingredient  no_hub


In [ ]:
ingredient_df = df[df['node_type'] == 'ingredient']

print(ingredient_df.head())

   node_id                    name  id   node_type  is_hub
0        0       1%_fat_buttermilk NaN  ingredient  no_hub
1        1   1%_fat_cottage_cheese NaN  ingredient  no_hub
2        3               10%_cream NaN  ingredient  no_hub
3        4               100%_bran NaN  ingredient  no_hub
4        5  10_inch_flour_tortilla NaN  ingredient  no_hub
      node_id               name  id   node_type  is_hub
6648     7097  za'atar_spice_mix NaN  ingredient  no_hub
6649     7098          zinfandel NaN  ingredient  no_hub
6650     7099         ziploc_bag NaN  ingredient  no_hub
6651     7100         ziti_pasta NaN  ingredient  no_hub
6652     7101           zucchini NaN  ingredient  no_hub


### 2. Creating file for labelling

Our goal was to train a model to substitute allergenic ingredients in recepies according to user preferences, we wanted to achieve that in process of supervised learning. Therefore, we needed to label data. Unfortunatelly we weren't able to find any dataset containg information about alergens beeing present in a food. We needed to label data on our own. We decided to label 800 examples and then create a model which will learn how to label other ingrediends basing on those 800 examples.

In [ ]:
shuffled_ingredient_df = ingredient_df.sample(frac=0.1203, random_state=10).reset_index(drop=True)

print(shuffled_ingredient_df)

     node_id                                    name  id   node_type  is_hub
0       2881                   gluten_free_soy_sauce NaN  ingredient  no_hub
1       4186                                  mezcal NaN  ingredient  no_hub
2       2725                          frozen_spinach NaN  ingredient  no_hub
3       2202                              elderberry NaN  ingredient     hub
4       4421                             nonfat_milk NaN  ingredient  no_hub
..       ...                                     ...  ..         ...     ...
795     6184  sugar_free_instant_vanilla_pudding_mix NaN  ingredient  no_hub
796     1730                                  crisco NaN  ingredient  no_hub
797      764                      buffalo_wing_sauce NaN  ingredient  no_hub
798     3680                            le_seuer_pea NaN  ingredient  no_hub
799     4994                           pork_rib_chop NaN  ingredient  no_hub

[800 rows x 5 columns]


We distinguished 9 types of labels: 'cows_milk', 'eggs', 'tree_nuts', 'peanuts', 'shellfish', 'wheat', 'soy', 'fish' - where 'wheat' we interpreted as a 'gluten'.

In [ ]:
new_df = shuffled_ingredient_df[['name']].copy()

new_columns = ['cows_milk', 'eggs', 'tree_nuts', 'peanuts', 'shellfish', 'wheat', 'soy', 'fish']
for column in new_columns:
    new_df[column] = 0

new_df.to_csv('output_file.csv', index=False)
print(new_df)

                                       name  cows_milk  eggs  tree_nuts  \
0                     gluten_free_soy_sauce          0     0          0   
1                                    mezcal          0     0          0   
2                            frozen_spinach          0     0          0   
3                                elderberry          0     0          0   
4                               nonfat_milk          0     0          0   
..                                      ...        ...   ...        ...   
795  sugar_free_instant_vanilla_pudding_mix          0     0          0   
796                                  crisco          0     0          0   
797                      buffalo_wing_sauce          0     0          0   
798                            le_seuer_pea          0     0          0   
799                           pork_rib_chop          0     0          0   

     peanuts  shellfish  wheat  soy  fish  
0          0          0      0    0     0  
1          

### \[Dugression\] An idea based on compounds and edges

Our first idea was to teach model how to label all examples according to compounds to which those ingredients were connected. This information were coded in 'edges_191120.csv' file.

In [ ]:
edges = pd.read_csv('edges_191120.csv')

'edges_191120.csv' data-set consists of 111359 rows and 4 columns: 'id_1', 'id_2' contain information about 2 nodes connected by an edge, 'score' informaes about similarity of nodes connected by one edge, 'edge_type' distinguished edges connecting two ingredients and edges connecting ingrediend with compound, the second type of connection was the most interesting for us.

In [ ]:
print(edges.head())

   id_1  id_2     score  edge_type
0  5063  6083  0.337742  ingr-ingr
1   244  4620  0.093855  ingr-ingr
2  2253  6753  0.107870  ingr-ingr
3  2813  6228  0.092569  ingr-ingr
4  3016  6314  0.123897  ingr-ingr


We filtered out all edges that was of type 'ingr-ingr' to leave only those which connects ingredients with their compounds.

In [ ]:
edges_df = edges[edges['edge_type'] != 'ingr-ingr']

In [ ]:
print(edges_df.head())

        id_1  id_2  score   edge_type
111355   685  7129    NaN  ingr-fcomp
111356   685  8119    NaN  ingr-fcomp
111357   685  7291    NaN  ingr-fcomp
111358   685  7518    NaN  ingr-fcomp
111359   685  7281    NaN  ingr-fcomp


Next step was to check how many unique ingrediends are connected to any of its compounds.

In [ ]:
compound_df = df[df['node_type'] == 'compound']

In [ ]:
print(compound_df.head())

      node_id            name        id node_type is_hub
6653     8192      naringenin  439246.0  compound   food
6654     8193    (-)-Limonene  439250.0  compound   food
6655     8194  (+)-Neomenthol  439263.0  compound   food
6656     8195   alpha-Maltose  439341.0  compound   food
6657     8196       Taxifolin  439533.0  compound   food


In [ ]:
edges2_df = edges[edges['id_2'] > 8191]

In [ ]:
print(len(edges2_df['id_1'].unique()))

409


We lost our enthusiasm when we found out that only 409 ingredients are connected to compound nodes. That was far to little to train any model on labeling ingredients. Morover nor of our 800 selected ingredients were connected to any compound.

In [ ]:
edges3_list = []
for i in edges2_df:
    if i[0] in shuffled_ingredient_df['node_id']:
        edges3_list.append(i)
print(edges3_list)

[]


In [ ]:
print(edges3_df)

Empty DataFrame
Columns: [id_1, id_2, score, edge_type]
Index: []


In [ ]:
connected_df = pd.DataFrame(0, columns=compound_df['node_id'], index=shuffled_ingredient_df['node_id'])

In [ ]:
print(connected_df.head())

node_id  8192  8193  8194  8195  8196  8197  8198  8199  8200  8201  ...  \
node_id                                                              ...   
2881        0     0     0     0     0     0     0     0     0     0  ...   
4186        0     0     0     0     0     0     0     0     0     0  ...   
2725        0     0     0     0     0     0     0     0     0     0  ...   
2202        0     0     0     0     0     0     0     0     0     0  ...   
4421        0     0     0     0     0     0     0     0     0     0  ...   

node_id  8694  8695  8696  8697  8698  8699  8700  8701  8702  8703  
node_id                                                              
2881        0     0     0     0     0     0     0     0     0     0  
4186        0     0     0     0     0     0     0     0     0     0  
2725        0     0     0     0     0     0     0     0     0     0  
2202        0     0     0     0     0     0     0     0     0     0  
4421        0     0     0     0     0     0    

### 3. Labeling examples by hand

As we mentioned before, we've created a file consisting of 800 examples. Each of us was responsible for labeling around 500 examples. We splited our work that way, that each example was labeled twice. Then we compared those examples to mark all differences in labeling. Every inconsistency was discissed and adjusted between us.

In [ ]:
import pandas as pd

file1 = pd.read_csv('file1.csv') #Labels created by Bogna
file2 = pd.read_csv('file2.csv') #Labels created by Adam
file3 = pd.read_csv('file3.csv') #Labels created by Maciej

def compare_rows(row1, row2):
    return all(row1 == row2)

differences = []

for i in range(1, 201):
    if not compare_rows(file1.iloc[i-1], file2.iloc[i-1]):
        differences.append(i)

for i in range(201, 500):
    if not compare_rows(file1.iloc[i-1], file3.iloc[i-1]):
        differences.append(i)

for i in range(501, 700):
    if not compare_rows(file2.iloc[i-1], file3.iloc[i-1]):
        differences.append(i)

for i in range(701, 800):
    if not compare_rows(file1.iloc[i-1], file2.iloc[i-1]):
        differences.append(i)

if not differences:
    print("No differences found.")
else:
    print("Differences found in rows:", differences)

Differences found in rows: [5, 13, 14, 24, 26, 27, 29, 31, 37, 39, 51, 52, 56, 57, 60, 63, 65, 70, 76, 88, 90, 91, 93, 97, 105, 107, 114, 127, 131, 133, 137, 141, 143, 153, 157, 158, 161, 163, 164, 166, 171, 175, 179, 182, 183, 186, 187, 189, 190, 226, 227, 229, 230, 232, 238, 239, 241, 243, 249, 252, 266, 269, 280, 288, 301, 302, 306, 311, 327, 339, 345, 349, 356, 361, 367, 375, 381, 387, 388, 405, 407, 425, 426, 428, 429, 431, 434, 436, 438, 439, 446, 449, 456, 458, 461, 462, 464, 465, 467, 472, 473, 478, 482, 483, 489, 501, 502, 503, 504, 505, 506, 507, 508, 509, 510, 511, 512, 513, 514, 515, 516, 517, 518, 519, 520, 521, 522, 523, 524, 525, 526, 527, 528, 529, 530, 531, 532, 533, 534, 535, 536, 537, 538, 539, 540, 541, 542, 543, 544, 545, 546, 547, 548, 549, 550, 551, 552, 553, 554, 555, 556, 557, 558, 559, 560, 561, 562, 563, 564, 565, 566, 567, 568, 569, 570, 571, 572, 573, 574, 575, 576, 577, 578, 579, 580, 581, 582, 583, 584, 585, 586, 587, 588, 589, 590, 591, 592, 593, 594, 59

In [ ]:
print(len(differences))

330


### 4. Preparing data to learning

Since our first idea was demented, we had to come up with something else. The second idea was to make a model which will learn about labels basing on the nodes most simmilar to particular ingredients.

In [ ]:
edges = pd.read_csv('edges_191120.csv')

In [ ]:
edges_df = edges[edges['edge_type'] == 'ingr-ingr']

In [ ]:
print(edges_df)

        id_1  id_2     score  edge_type
0       5063  6083  0.337742  ingr-ingr
1        244  4620  0.093855  ingr-ingr
2       2253  6753  0.107870  ingr-ingr
3       2813  6228  0.092569  ingr-ingr
4       3016  6314  0.123897  ingr-ingr
...      ...   ...       ...        ...
111350  4478  6458  0.101517  ingr-ingr
111351   938  6826  0.177222  ingr-ingr
111352  1363  6900  0.144170  ingr-ingr
111353   611  7035  0.119835  ingr-ingr
111354  1652  3899  0.251973  ingr-ingr

[111355 rows x 4 columns]


We filtered the edges list to leave only those edges which connect at least one of nodes in our prepared data set.

In [ ]:
edges3_list = []
for j, i in edges_df.iterrows():
    if i[0] in shuffled_ingredient_df['node_id'].tolist() or i[1] in shuffled_ingredient_df['node_id'].tolist():
        edges3_list.append(i)
print(edges3_list)

[id_1              5063
id_2              6083
score         0.337742
edge_type    ingr-ingr
Name: 0, dtype: object, id_1              2253
id_2              6753
score          0.10787
edge_type    ingr-ingr
Name: 2, dtype: object, id_1              3016
id_2              6314
score         0.123897
edge_type    ingr-ingr
Name: 4, dtype: object, id_1              1020
id_2              2901
score         0.167056
edge_type    ingr-ingr
Name: 5, dtype: object, id_1               500
id_2              4874
score         0.355899
edge_type    ingr-ingr
Name: 6, dtype: object, id_1              5763
id_2              6937
score         0.117413
edge_type    ingr-ingr
Name: 7, dtype: object, id_1               743
id_2              6434
score         0.304496
edge_type    ingr-ingr
Name: 13, dtype: object, id_1              2396
id_2              2556
score          0.04932
edge_type    ingr-ingr
Name: 30, dtype: object, id_1              4070
id_2              4465
score         0.178654


In [ ]:
print(len(edges3_list))

21897


In [ ]:
edges3_df = pd.DataFrame(edges3_list)

In [ ]:
print(edges3_df)

        id_1  id_2     score  edge_type
0       5063  6083  0.337742  ingr-ingr
2       2253  6753  0.107870  ingr-ingr
4       3016  6314  0.123897  ingr-ingr
5       1020  2901  0.167056  ingr-ingr
6        500  4874  0.355899  ingr-ingr
...      ...   ...       ...        ...
111328   268  3424  0.233139  ingr-ingr
111329   534  5775  0.181466  ingr-ingr
111333   181  4701  0.186159  ingr-ingr
111336  1682  2859  0.251909  ingr-ingr
111354  1652  3899  0.251973  ingr-ingr

[21897 rows x 4 columns]


Then we added one more condition: we left only those edges for which the similarity score was higher than 0.2.

In [ ]:
edges4_df = edges3_df[edges3_df['score'] > 0.2]

In [ ]:
print(edges4_df)

        id_1  id_2     score  edge_type
0       5063  6083  0.337742  ingr-ingr
6        500  4874  0.355899  ingr-ingr
13       743  6434  0.304496  ingr-ingr
41      1682  4812  0.200645  ingr-ingr
42      2172  5803  0.270435  ingr-ingr
...      ...   ...       ...        ...
111298  1049  1088  0.324034  ingr-ingr
111304  3793  5139  0.314777  ingr-ingr
111328   268  3424  0.233139  ingr-ingr
111336  1682  2859  0.251909  ingr-ingr
111354  1652  3899  0.251973  ingr-ingr

[10281 rows x 4 columns]


In [ ]:
ingredient2_df = ingredient_df.set_index(ingredient_df['node_id'])
ingredient2_df = ingredient2_df.drop(['node_id'], axis=1)
print(ingredient2_df)

                           name  id   node_type  is_hub
node_id                                                
0             1%_fat_buttermilk NaN  ingredient  no_hub
1         1%_fat_cottage_cheese NaN  ingredient  no_hub
3                     10%_cream NaN  ingredient  no_hub
4                     100%_bran NaN  ingredient  no_hub
5        10_inch_flour_tortilla NaN  ingredient  no_hub
...                         ...  ..         ...     ...
7097          za'atar_spice_mix NaN  ingredient  no_hub
7098                  zinfandel NaN  ingredient  no_hub
7099                 ziploc_bag NaN  ingredient  no_hub
7100                 ziti_pasta NaN  ingredient  no_hub
7101                   zucchini NaN  ingredient  no_hub

[6653 rows x 4 columns]


Then for each labeled ingredied we created a list containing this ingredient on 0th position and all ingredients connected with it.

In [ ]:
inputdata = []
for j, ingr in shuffled_ingredient_df.iterrows():
    temp = []
    temp.append(ingr[1])
    for i, e in edges4_df.iterrows():
        try:
            if e[0] == ingr[0]:
                temp.append(ingredient2_df['name'][e[1]])
            if e[1] == ingr[0]:
                temp.append(ingredient2_df['name'][e[0]])
        except:
            continue
    inputdata.append(temp)

In [ ]:
print(inputdata[0])

['gluten_free_soy_sauce', 'sesame_oil', 'fresh_ginger', 'rice_vinegar', 'sesame_seed']


In [ ]:
input_df = pd.DataFrame(inputdata)

We've saved the created dataset as a csv file.

In [ ]:
input_df.to_csv('inputdata.csv', index=False)

In [3]:
input_df = pd.read_csv('inputdata.csv')

In [ ]:
input_list = []
for i in range(len(input_df)):
    input_list.append(input_df.iloc[i].unique().tolist()[:-1])
input_list

[['gluten_free_soy_sauce',
  'sesame_oil',
  'fresh_ginger',
  'rice_vinegar',
  'sesame_seed'],
 ['mezcal',
  'orange_twist',
  'angostura_bitter',
  'tequila',
  'fresh_lime_juice',
  'bitter',
  'ice',
  'triple_sec',
  'orange_bitter',
  'simple_syrup',
  'lime_wedge',
  'agave_nectar'],
 ['frozen_spinach',
  'vegetable_soup_mix',
  'alfredo_sauce',
  'whole_wheat_lasagna_noodle',
  'artichoke_heart',
  'no_boil_lasagna_noodle',
  'knorr_vegetable_soup_mix',
  'fat_free_cottage_cheese',
  'cottage_cheese',
  'marinated_artichoke',
  'dry_vegetable_soup_mix',
  'canned_artichoke_heart',
  'parmesan_cheese',
  'jumbo_pasta_shell',
  'italian_turkey_sausage',
  'pasta_sauce',
  'fat_free_ricotta_cheese',
  'simply_potatoes_shredded_hash_brown',
  'laughing_cow_cheese',
  'simply_potatoes_traditional_mashed_potato',
  'manicotti',
  'italian_cheese_blend',
  'hidden_valley_original_ranch_seasoning_mix',
  'lasagna_sheet',
  'phyllo_pastry',
  'water_packed_artichoke_heart',
  'ricotta_

Then we've made sure that each list has the same size. To achieve that we truncated some listst to 5 first positions or we added 'nan' values if the list has lenght less than 5.

In [6]:
x = []
for i in range(len(input_df)):
    x.append(input_df.iloc[i].tolist()[:5])
x

[['gluten_free_soy_sauce',
  'sesame_oil',
  'fresh_ginger',
  'rice_vinegar',
  'sesame_seed'],
 ['mezcal', 'orange_twist', 'angostura_bitter', 'tequila', 'fresh_lime_juice'],
 ['frozen_spinach',
  'vegetable_soup_mix',
  'alfredo_sauce',
  'whole_wheat_lasagna_noodle',
  'artichoke_heart'],
 ['elderberry', 'cinnamon_stick', nan, nan, nan],
 ['nonfat_milk',
  'fat_free_liquid_egg_product',
  'fat_free_cheddar_cheese',
  'vanilla_protein_powder',
  'reduced_fat_margarine'],
 ['ground_basil', 'white_pepper', 'onion_powder', 'ground_thyme', 'oregano'],
 ['beef_tongue', 'whole_clove', 'black_peppercorn', 'peppercorn', 'bay_leaf'],
 ['mustard_vinaigrette', 'dijon_mustard', nan, nan, nan],
 ['pepper_vinegar', nan, nan, nan, nan],
 ['peaches_in_light_syrup', 'almond', 'low_fat_vanilla_yogurt', nan, nan],
 ['italian_style_tomato_paste', 'dried_oregano', nan, nan, nan],
 ['porterhouse_steak', 'yukon_gold_potato', 'fresh_rosemary', nan, nan],
 ['dark_roast_coffee', 'chocolate_syrup', nan, nan, 

### 5. Creating model

We've decied to use the TensorFlow library to create a model.

In [5]:
from tensorflow import keras
from sklearn.metrics import accuracy_score, precision_score, recall_score

As a target we took created by us labels. We've converted it to boolean type.

In [15]:
y = pd.read_csv('swsnlabels - file1.csv')

In [16]:
y.iloc[:, 1:] = y.iloc[:, 1:].astype(bool)
y

name  cows_milk   eggs  tree_nuts  \
0                     gluten_free_soy_sauce      False  False      False   
1                                    mezcal      False  False      False   
2                            frozen_spinach      False  False      False   
3                                elderberry      False  False      False   
4                               nonfat_milk       True  False      False   
..                                      ...        ...    ...        ...   
795  sugar_free_instant_vanilla_pudding_mix      False  False      False   
796                                  crisco      False  False      False   
797                      buffalo_wing_sauce       True  False      False   
798                            le_seuer_pea      False  False      False   
799                           pork_rib_chop      False  False      False   

     peanuts  shellfish  wheat    soy   fish  
0      False      False  False   True  False  
1      False      False  False  False  False  
2      False      False  False  False  False  
3      False      False  False  False  False  
4      False      False   True  False  False  
..       ...        ...    ...    ...    ...  
795    False      False  False  False  False  
796    False      False  False  False  False  
797    False      False   True  False   True  
798    False      False  False  False  False  
799    False      False  False  False  False  

[800 rows x 9 columns]

In [17]:
y2 = []
for i in range(len(y)):
    y2.append(y.iloc[i].tolist())
y2

[['gluten_free_soy_sauce',
  False,
  False,
  False,
  False,
  False,
  False,
  True,
  False],
 ['mezcal', False, False, False, False, False, False, False, False],
 ['frozen_spinach', False, False, False, False, False, False, False, False],
 ['elderberry', False, False, False, False, False, False, False, False],
 ['nonfat_milk', True, False, False, False, False, True, False, False],
 ['ground_basil', False, False, False, False, False, False, False, False],
 ['beef_tongue', False, False, False, False, False, False, False, False],
 ['mustard_vinaigrette',
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False],
 ['pepper_vinegar', False, False, False, False, False, False, False, False],
 ['peaches_in_light_syrup',
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False],
 ['italian_style_tomato_paste',
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False],
 ['porterhouse_steak', False, False, False, False, False, False, False, False],


In [22]:
y = y2

In [24]:
print(y)

[['gluten_free_soy_sauce', False, False, False, False, False, False, True, False], ['mezcal', False, False, False, False, False, False, False, False], ['frozen_spinach', False, False, False, False, False, False, False, False], ['elderberry', False, False, False, False, False, False, False, False], ['nonfat_milk', True, False, False, False, False, True, False, False], ['ground_basil', False, False, False, False, False, False, False, False], ['beef_tongue', False, False, False, False, False, False, False, False], ['mustard_vinaigrette', False, False, False, False, False, False, False, False], ['pepper_vinegar', False, False, False, False, False, False, False, False], ['peaches_in_light_syrup', False, False, False, False, False, False, False, False], ['italian_style_tomato_paste', False, False, False, False, False, False, False, False], ['porterhouse_steak', False, False, False, False, False, False, False, False], ['dark_roast_coffee', False, False, False, False, False, False, False, Fals

In [46]:
x = np.asarray([x])
y = np.asarray(y)

We've splitted data into traing, validation and test sets. Training set contains 60% of all examples, validation set - 20% of examples, same as test set.

In [48]:
idx = np.arange(len(x))
np.random.shuffle(idx)
split_1 = int(6/10 * len(x))
split_2 = int(8/10 * len(x))

train_x, train_y = x[idx[ : split_1]], y[idx[ : split_1]]
val_x, val_y = x[idx[split_1 : split_2]], y[idx[split_1 : split_2]]
test_x, test_y = x[idx[split_2 : ]], y[idx[split_2 : ]]

In [27]:
import tensorflow as tf
from tensorflow.keras.layers import Dense, Input, concatenate, Concatenate, LSTM
from tensorflow.keras.models import Model, Sequential
from tensorflow.keras.utils import Sequence, plot_model
from tensorflow.keras.callbacks import EarlyStopping, ReduceLROnPlateau

In [47]:
print(x.shape)

(1, 800, 5)


We've atempted to create a sequential model. However we've benn struggling with some errors related to dimensions of data transfered between layers. Therefore we've never finnished the training.

In [49]:
model = Sequential()
model.add(Input(shape = (None, 5)))
model.add(LSTM(64, return_sequences=True))
model.add(LSTM(16, return_sequences=False))
model.add(Dense(9, activation='sigmoid'))
model.summary()
model.compile(loss='binary_crossentropy', metrics=['acc', 'recall', 'precision'])

Model: "sequential_8"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm_13 (LSTM)              (None, None, 64)          17920     
                                                                 
 lstm_14 (LSTM)              (None, 16)                5184      
                                                                 
 dense_5 (Dense)             (None, 9)                 153       
                                                                 
Total params: 23257 (90.85 KB)
Trainable params: 23257 (90.85 KB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________


In [34]:
print(x.shape)

(800, 5)


In [50]:
[print(i.shape, i.dtype) for i in model.inputs]
[print(o.shape, o.dtype) for o in model.outputs]

(None, None, 5) <dtype: 'float32'>
(None, 9) <dtype: 'float32'>


[None]

In [51]:
print(train_x.shape, train_x.dtype)
print(train_y.shape, train_y.dtype)

(0, 800, 5) <U69
(0, 9) <U47


In [52]:
early = EarlyStopping(patience=7, restore_best_weights=True)
model.fit(train_x,train_y, batch_size=256, epochs=5, validation_data=(val_x, val_y), callbacks=[early])

ValueError: Expected input data to be non-empty.